# Pipeline 1
+ knowledge base
+ training
+ evaluation
+ vector database
+ rag

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
!pip install python-dotenv

In [3]:
from dotenv import load_dotenv
load_dotenv("/content/drive/Shareddrives/Knowledge Graph/code/pipeline/.env", override=True)

True

## Knowledge base
In this component we perform the loading of the knowledge base

In [21]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/0.knowledge_base
!pip install -r requirements.txt

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/0.knowledge_base
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 567.0/567.0 kB 11.7 MB/s eta 0:00:00


In [22]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


In [23]:
import os
import random
import pickle
import rdflib

def knowledge_base():
    def parse_rdf(file_path):
        g = rdflib.Graph()
        try:
            g.parse(file_path, format='ttl')
        except rdflib.exceptions.ParserError as e:
            print(f"Errore di parsing: {e}")
        triples = [(str(s), str(p), str(o)) for s, p, o in g]
        return triples

    input_path = os.getenv('input_path')
    output_path = os.getenv('output_path')

    rdf_triples = parse_rdf(input_path)

    random.shuffle(rdf_triples)
    num_triples = len(rdf_triples)
    train_size = int(0.8 * num_triples)
    valid_size = int(0.1 * num_triples)
    test_size = num_triples - train_size - valid_size

    train_triples = rdf_triples[:train_size]
    valid_triples = rdf_triples[train_size:train_size + valid_size]
    test_triples = rdf_triples[train_size + valid_size:]

    print(f'Number of triples in the training set: {len(train_triples)}')
    print(f'Number of triples in the validation set: {len(valid_triples)}')
    print(f'Number of triples in the test set: {len(test_triples)}')

    with open(output_path, 'wb') as f:
        pickle.dump((train_triples, valid_triples, test_triples), f)

if __name__ == "__main__":
    knowledge_base()


Number of triples in the training set: 25048
Number of triples in the validation set: 3131
Number of triples in the test set: 3131


## Training
In this component we perform the training of a knowledge graph embedding model (e.g. TransE) on the knowledge base loaded previously

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/1.training
!pip install -r requirements.txt

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


### Hyper-parameters optimization

In [ ]:
import os
import pickle
import numpy as np
import torch
from pykeen.hpo import hpo_pipeline
from pykeen.triples import TriplesFactory
from pykeen.trackers import TensorBoardResultTracker
from optuna.samplers import TPESampler

def hpo_train():
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"Using device: {device}")

    # Caricamento dei dati
    with open(os.getenv('output_path'), 'rb') as f:
        train_triples, valid_triples, test_triples = pickle.load(f)

    # Creazione dei TriplesFactory
    train_tf = TriplesFactory.from_labeled_triples(np.array(train_triples))
    valid_tf = TriplesFactory.from_labeled_triples(np.array(valid_triples))
    test_tf = TriplesFactory.from_labeled_triples(np.array(test_triples))

    # Configurazione del risultato tracker per TensorBoard
    tracker = TensorBoardResultTracker(
        experiment_path=os.getenv('TENSORBOARD_PATH_ARCH'),
        experiment_name='TransE_HPO'
    )

    # Configurazione HPO
    hpo_result = hpo_pipeline(
        model='TransE',
        training=train_tf,       # Fornire il TriplesFactory di training
        validation=valid_tf,     # Fornire il TriplesFactory di validazione
        testing=test_tf,         # Fornire il TriplesFactory di test
        training_kwargs=dict(
            num_epochs=50,  # Numero di epoche massimo durante l'HPO
            checkpoint_directory='./hpo_checkpoints',
            checkpoint_frequency=10,
        ),
        evaluator_kwargs=dict(filtered=True),  # Per valutazioni filtrate
        result_tracker=tracker,
        sampler=TPESampler(seed=42),  # Metodo TPE per l'ottimizzazione
        model_kwargs_ranges=dict(
            embedding_dim=dict(type=int, low=16, high=256, step=32)
        ),
        optimizer_kwargs_ranges=dict(
            lr=dict(type=float, low=0.0001, high=0.1, scale='log')
        ),
        n_trials=20,  # Numero di esperimenti
        timeout=3600,  # Tempo massimo in secondi
    )


    best_params = hpo_result.study.best_trial.params
    output_file = "./training/best_params.txt"

    with open(output_file, "w") as file:
        file.write("Best parameters:\n")
        for param, value in best_params.items():
            file.write(f"{param}: {value}\n")

    print(f"Best parameters have been saved to {output_file}")

if __name__ == "__main__":
    hpo_train()


### Training with dataset from file

In [ ]:
import os
import torch
from pykeen.datasets import PathDataset
from pykeen.pipeline import pipeline
from pykeen.evaluation import RankBasedEvaluator
from pykeen.losses import MarginRankingLoss
from pykeen.trackers import TensorBoardResultTracker
from pykeen.models import TransE
from pykeen.training import SLCWATrainingLoop
from pykeen.sampling import BasicNegativeSampler
from pykeen.triples import TriplesFactory
import pykeen.models
import pickle
import numpy as np


def train():
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"Using device: {device}")
    embedding_dim = int(os.getenv('EMBEDDING_DIM'))
    num_epochs = int(os.getenv('NUM_EPOCHS'))
    learning_rate = float(os.getenv('LEARNING_RATE'))
    num_negs_per_pos = int(os.getenv('NUM_NEGS_PER_POS'))
    model_name = os.getenv('MODEL')
    training_loop = os.getenv('TRAINING_LOOP')
    optimizer = os.getenv('OPTIMIZER')
    batch_size = os.getenv('BATCH_SIZE')

    with open(os.getenv('output_path_arch'), 'rb') as f:
        train_triples, valid_triples, test_triples = pickle.load(f)

    all_triples = train_triples + valid_triples + test_triples
    train_triples_np = np.array(all_triples)
    train_tf = TriplesFactory.from_labeled_triples(train_triples_np)

    tracker = TensorBoardResultTracker(experiment_path=os.getenv('TENSORBOARD_PATH_ARCH'), experiment_name=model_name)

    model_class = getattr(pykeen.models, model_name)

    model = model_class(
        triples_factory=train_tf,
        embedding_dim=1536,
        random_seed=42,
        loss="MarginRankingLoss",
        ).to(device)
    negative_sampler = BasicNegativeSampler(
        mapped_triples = train_tf.mapped_triples,
        num_negs_per_pos=num_negs_per_pos)

    training_loop = SLCWATrainingLoop(
        triples_factory=train_tf,
        model = model,
        optimizer=optimizer,
        optimizer_kwargs=dict(lr=learning_rate),
        result_tracker = tracker,
        negative_sampler = negative_sampler,
    )

    checkpoint_directory = './training'
    checkpoint_frequency = 10

    training_loop.train(
        triples_factory=train_tf,
        num_epochs = num_epochs,
        checkpoint_name = os.getenv('CHECKPOINT_NAME_ARCH'),
        checkpoint_directory=checkpoint_directory,
        batch_size=512,
        checkpoint_frequency=checkpoint_frequency,
    )

    model_path = os.getenv('MODEL_PATH_ARCH')
    with open(model_path, 'wb') as file:
      pickle.dump(model, file)

    return model

if __name__ == "__main__":
    model = train()

INFO:pykeen.nn.representation:Inferred unique=False for Embedding()
INFO:pykeen.nn.representation:Inferred unique=False for Embedding()
INFO:pykeen.training.training_loop:=> no checkpoint found at 'training/checkpoint_arch.pt'. Creating a new file.


Using device: cuda


Training epochs on cuda:0:   0%|          | 0/580 [00:00<?, ?epoch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

...

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

INFO:pykeen.training.training_loop:=> Saved checkpoint after having finished epoch 580.


## Evaluation
In this component we perform the evaluation of the trained model

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/2.evaluation
!pip install -r requirements.txt

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/2.evaluation
  Cloning https://github.com/pykeen/pykeen.git to /tmp/pip-req-build-368t8ngi
  Running command git clone --filter=blob:none --quiet https://github.com/pykeen/pykeen.git /tmp/pip-req-build-368t8ngi
  Resolved https://github.com/pykeen/pykeen.git to commit 0eb14895ebc5d803f268fa23a0b5504a255ca3a9
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


### Evaluation with dataset from file

In [ ]:
import json
import torch
import os
import pickle
from pykeen.evaluation import RankBasedEvaluator
from pykeen.triples import TriplesFactory
import pykeen.models

def evaluate():
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"Using device: {device}")

    model_name = os.getenv('MODEL')
    model_path = os.getenv('MODEL_PATH')

    model_class = getattr(pykeen.models, model_name)
    with open(model_path, 'rb') as file:
        model = pickle.load(file)
    model = model.to(device)

    with open(os.getenv('output_path'), 'rb') as f:
        train_triples, valid_triples, test_triples = pickle.load(f)


    train_triples_np = np.array(train_triples)
    valid_triples_np = np.array(valid_triples)
    test_triples_np = np.array(test_triples)
    train_tf = TriplesFactory.from_labeled_triples(train_triples_np)
    valid_tf = TriplesFactory.from_labeled_triples(valid_triples_np)
    test_tf = TriplesFactory.from_labeled_triples(test_triples_np)

    evaluator = RankBasedEvaluator(
        metrics=["hits_at_k"],
        metrics_kwargs=[dict(k=100)],
        filtered=True)

    additional_filter_triples = [
        train_tf.mapped_triples,
        test_tf.mapped_triples,
    ]

    validation_results = evaluator.evaluate(
        model=model,
        mapped_triples=valid_tf.mapped_triples,
        additional_filter_triples=additional_filter_triples,
    )

    selected_validation_metrics = {
    'hits@1': validation_results.get_metric('hits@1'),
    'hits@3': validation_results.get_metric('hits@3'),
    'hits@5': validation_results.get_metric('hits@5'),
    'hits@10': validation_results.get_metric('hits@10'),
    'hits@100': validation_results.get_metric('hits@100'),
    'MRR': validation_results.get_metric('mean_reciprocal_rank')
    }


    validation_results_path = os.getenv('VALIDATION_RESULTS_PATH')
    with open(validation_results_path, 'w') as f:
        json.dump(selected_validation_metrics, f, indent=4)

    print(f"Validation results saved to {validation_results_path}")

    additional_filter_triples = [
        train_tf.mapped_triples,
        valid_tf.mapped_triples,
    ]

    test_results = evaluator.evaluate(
        model=model,
        mapped_triples=test_tf.mapped_triples,
        additional_filter_triples=additional_filter_triples,
    )

    selected_test_metrics = {
    'hits@1': test_results.get_metric('hits@1'),
    'hits@3': test_results.get_metric('hits@3'),
    'hits@5': test_results.get_metric('hits@5'),
    'hits@10': test_results.get_metric('hits@10'),
    'hits@100': test_results.get_metric('hits@100'),
    'MRR': test_results.get_metric('mean_reciprocal_rank')
    }

    test_results_path = os.getenv('TEST_RESULTS_PATH')
    with open(test_results_path, 'w') as f:
        json.dump(selected_test_metrics, f, indent=4)

    print(f"Test results saved to {test_results_path}")

if __name__ == "__main__":
    evaluate()


Using device: cuda


Evaluating on cuda:0:   0%|          | 0.00/3.13k [00:00<?, ?triple/s]

INFO:pykeen.evaluation.evaluator:Evaluation took 8.92s seconds


Validation results saved to ./evaluation/validation_results_TransE_d3fend.txt


Evaluating on cuda:0:   0%|          | 0.00/3.13k [00:00<?, ?triple/s]

INFO:pykeen.evaluation.evaluator:Evaluation took 8.88s seconds


Test results saved to ./evaluation/test_results_TransE_hetionet_250ep.txt


## Embeddings
In this component we perform the extraction of the embeddings from the trained model

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/3.vector_database
!pip install -r requirements.txt

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


### Vector database with database from file

In [ ]:

import re
import torch
import time
import os
import numpy as np
import json
import pykeen.models
import pandas as pd
import pickle

def extract_name(url):
    prefixes = [
        "http://d3fend.mitre.org/ontologies/d3fend.owl#",
        "http://www.w3.org/2000/01/rdf-schema#",
        "http://example.org/entities/",
        "http://example.org/d3f/",
        "http://www.w3.org/1999/02/22-rdf-syntax-ns#",
        "http://www.w3.org/2002/07/owl#",
        "http://www.w3.org/2004/02/skos/core#"
    ]
    for prefix in prefixes:
        if url.startswith(prefix):
            return re.split(r'[#/]', url)[-1]
    return url

# Funzione per normalizzare i vettori
def normalize_vector(v):
    return v / np.linalg.norm(v)

# Funzione per scrivere i dati su file JSON
def write_to_file(filename, data):
    with open(filename, 'w') as file:
        json.dump(data, file, indent=4)

def embeddings():
  device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
  print(f"Using device: {device}")

  model_name = os.getenv('MODEL')
  model_path = os.getenv('MODEL_PATH_ARCH')

  model_class = getattr(pykeen.models, model_name)
  with open(model_path, 'rb') as file:
      model = pickle.load(file)
  model = model.to(device)

  entity_embeddings = model.entity_representations[0](indices=None)
  relation_embeddings = model.relation_representations[0](indices=None)

  entity_embeddings_cpu = entity_embeddings.detach().cpu()
  relation_embeddings_cpu = relation_embeddings.detach().cpu()

  entity_embeddings_list = entity_embeddings_cpu.numpy().tolist()
  relation_embeddings_list = relation_embeddings_cpu.numpy().tolist()


  with open(os.getenv('output_path_arch'), 'rb') as f:
      train_triples, valid_triples, test_triples = pickle.load(f)
  all_triples = train_triples+valid_triples+test_triples
  all_triples_np = np.array(all_triples)
  from pykeen.triples import TriplesFactory
  triples_factory = TriplesFactory.from_labeled_triples(all_triples_np)

  entity_to_id = triples_factory.entity_to_id
  relation_to_id = triples_factory.relation_to_id

  entity_embeddings_dict_TransE = {entity: entity_embeddings_list[idx] for entity, idx in entity_to_id.items()}
  relation_embeddings_dict_TransE = {relation: relation_embeddings_list[idx] for relation, idx in relation_to_id.items()}

  entity_keys = entity_to_id.keys()
  relation_keys = relation_to_id.keys()

  from langchain_openai import OpenAIEmbeddings
  from sklearn.decomposition import PCA
  from sklearn.linear_model import LinearRegression

  embedding_model = OpenAIEmbeddings(
    api_key=os.getenv("OPENAI_API_TOKEN"),
    model="text-embedding-ada-002",
  )
  entity_embeddings_openai = embedding_model.embed_documents(entity_keys)
  relation_embeddings_openai = embedding_model.embed_documents(relation_keys)

  entity_embeddings_dict_openai = {key: embedding for key, embedding in zip(entity_keys, entity_embeddings_openai)}
  relation_embeddings_dict_openai = {key: embedding for key, embedding in zip(relation_keys, relation_embeddings_openai)}

  common_entities = set(entity_embeddings_dict_TransE.keys()) & set(entity_embeddings_dict_openai.keys())
  transE_entity_vectors = [entity_embeddings_dict_TransE[e] for e in common_entities]
  openai_entity_vectors = [entity_embeddings_dict_openai[e] for e in common_entities]

  transE_array_entity = np.array(transE_entity_vectors)
  openai_array_entity = np.array(openai_entity_vectors)
  reg = LinearRegression()
  reg.fit(transE_array_entity, openai_array_entity)
  W = reg.coef_


  transE_aligned_entity = transE_array_entity @ W.T

  # Salvare gli embedding allineati in JSON
  aligned_entity_dict = {entity: embedding.tolist() for entity, embedding in zip(common_entities, transE_aligned_entity)}

  with open("./vector_database/transE_aligned_entity_arch.json", "w") as file:
      json.dump(aligned_entity_dict, file, indent=4)

  print("Embedding delle entità allineati salvati in transE_aligned_entity.json!")


  common_relations = set(relation_embeddings_dict_TransE.keys()) & set(relation_embeddings_dict_openai.keys())
  transE_relation_vectors = [relation_embeddings_dict_TransE[e] for e in common_relations]
  openai_relation_vectors = [relation_embeddings_dict_openai[e] for e in common_relations]

  transE_array_relation = np.array(transE_relation_vectors)
  openai_array_relation = np.array(openai_relation_vectors)
  reg = LinearRegression()
  reg.fit(transE_array_relation, openai_array_relation)
  W = reg.coef_


  transE_aligned_relation = transE_array_relation @ W.T


  # Salvare gli embedding allineati in JSON
  aligned_relation_dict = {relation: embedding.tolist() for relation, embedding in zip(common_relations, transE_aligned_relation)}

  with open("./vector_database/transE_aligned_relation_arch.json", "w") as file:
      json.dump(aligned_relation_dict, file, indent=4)

  print("Embedding delle relazioni allineati salvati in transE_aligned_relation.json!")


if __name__ == "__main__":
    embeddings()


Using device: cuda
16
16
Embedding delle entità allineati salvati in transE_aligned_entity.json!
Embedding delle relazioni allineati salvati in transE_aligned_relation.json!


## RAG
In this component we perform a Retrieval Augmented Generation from the data loaded in Weaviate

In [4]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/4.rag
!pip install -r requirements.txt

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/4.rag
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 28.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 330.4/330.4 kB 15.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.5/43.5 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.2/54.2 kB 4.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 223.8/223.8 kB 15.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 55.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.1/519.1 kB 21.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 39.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 319.7/319.7 kB 17.8 MB/s eta 0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 4.25.5
    Uninstalling protobuf-4.25.5:
      Successfully uninstalled 

In [5]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


In [10]:
import os
from langchain_openai import ChatOpenAI
from langchain_openai import OpenAIEmbeddings
import textwrap
import numpy as np
import re
from sklearn.metrics.pairwise import cosine_similarity
import pickle
import json

def rag():
    # Funzione per caricare i dati JSON
    def load_embeddings(file_path):
        with open(file_path, 'r') as file:
            return json.load(file)

    def extract_name(url):
        prefixes = [
            "http://d3fend.mitre.org/ontologies/d3fend.owl#",
            "http://www.w3.org/2000/01/rdf-schema#",
            "http://example.org/entities/",
            "http://example.org/d3f/",
            "http://www.w3.org/1999/02/22-rdf-syntax-ns#",
            "http://www.w3.org/2002/07/owl#",
            "http://www.w3.org/2004/02/skos/core#"
        ]
        for prefix in prefixes:
            if url.startswith(prefix):
                return re.split(r'[#/]', url)[-1]
        return url

    # Funzione per fare la similarity search
    def similarity_search(question, path_similarity):
        # Carica gli embedding dal file JSON
        embeddings_data = load_embeddings(path_similarity)

        embedding_model = OpenAIEmbeddings(
            api_key=os.getenv("OPENAI_API_TOKEN"),
            model="text-embedding-ada-002",
        )
        query_vector = embedding_model.embed_query(question)

        # Calcola la similarità per ciascun embedding
        similarities = []
        for entity, embedding in embeddings_data.items():
            entity_name = entity
            embedding = np.array(embedding)
            similarity = cosine_similarity(query_vector, embedding)
            similarities.append((entity_name, similarity))


        # Ordina per similarità decrescente
        similarities.sort(key=lambda x: x[1], reverse=True)

        # Restituisci i top_k risultati
        return similarities[:4]

    # Funzione per generare una risposta dal modello LLM
    def generate_RAG_answer(question: str, context: str):
        llm = ChatOpenAI(
            temperature=0,
            api_key=os.getenv("OPENAI_API_TOKEN"),
            model_name="gpt-3.5-turbo"
        )
        prompt = f"Answer the question based on the context: \n\nContext: {context}\n\nQuestion: {question}"
        response = llm.invoke(prompt)
        return response.content

        # Funzione per generare una risposta dal modello LLM
    def generate_LLM_answer(question: str):
        llm = ChatOpenAI(
            temperature=0,
            api_key=os.getenv("OPENAI_API_TOKEN"),
            model_name="gpt-3.5-turbo"
        )
        response = llm.invoke(question)
        return response.content

    def get_context(question, path_get_context, path_similarity):
        context = []
        results = similarity_search(question, path_similarity)
        # Carica i dati dal file pickle
        with open(path_get_context, 'rb') as f:
            train_triples, valid_triples, test_triples = pickle.load(f)

        # Combina tutte le triple
        all_triples = train_triples + valid_triples + test_triples

        # Crea una nuova lista di triple con i valori aggiornati
        processed_triples = [
            (extract_name(triple[0]), extract_name(triple[1]), extract_name(triple[2]))
            for triple in all_triples
        ]
        # Elaborazione
        for entity_name, similarity in results:
            # Rimuove gli spazi dal primo elemento della tupla
            normalized_entity_name = entity_name.replace(" ", "")

            # Filtra le triple che corrispondono al target_string
            filtered_triples = [
                triple for triple in processed_triples
                if triple[0] == extract_name(normalized_entity_name) or triple[2] == extract_name(normalized_entity_name)
            ]

            # Aggiunge i risultati al contesto
            context.append((filtered_triples, similarity))

        return results,context

    # Funzione per stampare i risultati in un formato leggibile
    def pretty_print_response(question: str, dataset:str):
        print(f"Question: {question}")
        print("=" * 90)
        if dataset == "d3fend":
          path_get_context = os.getenv('output_path')
          path_similarity = os.getenv("embeddings_file")
        else:  # 'architecture'
          path_get_context = os.getenv('output_path_arch')
          path_similarity = os.getenv("embeddings_file_arch")
        context, triples = get_context(question, path_get_context, path_similarity)
        print("Similarity Search Entities:")
        print(context)
        print("=" * 90)
        print("Similarity Search Triples:")
        print(triples)
        print("=" * 90)
        # Genera la risposta basata sul contesto
        answer = generate_RAG_answer(question, triples)
        print("=" * 90)
        print("RAG Answer:")
        print(textwrap.fill(answer, 60))
        print("=" * 90)
        print("LLM Answer:")
        print(textwrap.fill(generate_LLM_answer(question), 60))
        print("=" * 90)

    """
    question = "What does the user do in my architecture?"
    pretty_print_response(question)
    print("--------------------------------------------------------------------------------------")
    question2 = "How many types of mail servers do I have in my architecture?"
    pretty_print_response(question2)
    print("--------------------------------------------------------------------------------------")
    question3 = "Which mail server retrieves emails for the user?"
    pretty_print_response(question3)
    print("--------------------------------------------------------------------------------------")
    question4 = "Is IMAP used for retrieving emails?"
    pretty_print_response(question4)
    """
    question = "What is the definition of PacketLog?"
    dataset = "d3fend"
    pretty_print_response(question, dataset)
    print("--------------------------------------------------------------------------------------")

if __name__ == "__main__":
    rag()

Question: What is the definition of PacketLog?
Similarity Search Entities:
[('Packet Log', 0.17837716221562014), ('Log', 0.15298246365145274), ('Network Packet', 0.15004475299639075), ('http://d3fend.mitre.org/ontologies/d3fend.owl#PacketLog', 0.1495983320419706)]
Similarity Search Triples:
[([('PacketLog', 'type', 'http://www.w3.org/2002/07/owl#NamedIndividual'), ('PacketLog', 'label', 'Packet Log'), ('PacketLog', 'seeAlso', 'http://dbpedia.org/resource/Packet_analyzer'), ('PacketLog', 'records', 'NetworkSession'), ('PacketLog', 'subClassOf', 'Log'), ('PacketLog', 'definition', 'A log of all the network packet data captured from a network by a network sensor (i.e., packet analyzer),'), ('PacketLog', 'type', 'http://www.w3.org/2002/07/owl#Class'), ('PacketLog', 'subClassOf', 'n520c131f7af149a8a4457963d1df1966b44')], 0.17837716221562014), ([('AuthenticationLog', 'subClassOf', 'Log'), ('Log', 'label', 'Log'), ('n520c131f7af149a8a4457963d1df1966b57', 'http://www.w3.org/2002/07/owl#someVal